In [117]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [5]:
!pip install -U sentence-transformers

In [105]:
import random
import os
import re
import pandas as pd
import numpy as np
from tqdm.auto import tqdm
import torch
from transformers import GPT2LMHeadModel, PreTrainedTokenizerFast
from transformers import AutoTokenizer, AutoModelForCausalLM
from sentence_transformers import SentenceTransformer

def reset_seeds(seed):
    random.seed(seed)
    os.environ['PYTHONHASHSEED'] = str(seed)
    np.random.seed(seed)
    torch.manual_seed(seed)
    torch.cuda.manual_seed(seed)
    torch.backends.cudnn.deterministic = True

DATA_PATH = '/content/drive/MyDrive/AI ML/DACON HANSOL/data/'
SUBMISSION_PATH = '/content/drive/MyDrive/AI ML/DACON HANSOL/data/'

SEED = 42
reset_seeds(SEED)
device = 'cuda' if torch.cuda.is_available() else 'cpu'
device

'cuda'

# 데이터

In [106]:
test_sim2.to_csv('test_sim3.csv', index=False)

In [118]:
valid_sim2 = pd.read_csv(f'{DATA_PATH}valid_sim2.csv')
valid_sim2

id                                                 질문  \
0    TEST_000  방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용...   
1    TEST_001            도배지에 녹은 자국이 발생하는 주된 원인과 그 해결 방법은 무엇인가요?   
2    TEST_002    큐블럭의 단점을 알려주세요. 또한, 압출법 단열판을 사용하는 것의 장점은 무엇인가요?   
3    TEST_003  철골구조를 사용하는 고층 건물에서, 단열 효과를 높이기 위한 시공 방법은 무엇이 있...   
4    TEST_004                   도배지의 완전한 건조를 위해 몇 주 동안 기다려야 하나요?   
..        ...                                                ...   
125  TEST_125  분말 소화기를 사용할 때 주의해야 할 사항은 무엇인가요? 그리고 아파트 도배 평수를...   
126  TEST_126                           압출법 보온판의 가장 큰 장점은 무엇인가요?   
127  TEST_127  평지붕의 누수 문제를 방지하기 위해 수성 벽체용 탄성 방수 도료를 사용하는 것이 어...   
128  TEST_128  석고수정이 발생하는 가장 큰 원인은 무엇인가요? 그리고 이를 해결하는 방법에 대해 ...   
129  TEST_129     카페트의 기대 수명은 얼마나 될까요? 그리고 오리지널징크의 장점에는 무엇이 있나요?   

                                                 유사_답변  
0    방청 페인트는 다양한 종류로 분류됩니다. 그 종류에는 광명단 페인트, 방청산화철 페...  
1    도배지에 녹이 묻어나오는 것은 녹오염으로, 도배지 상에 녹색 또는 갈색의 녹이 발생...  
2    큐블럭은 일반 벽돌에 비해 높은 비용과 균열이 쉽게 생길 수 있는 점, 그리고 습기...  
3    단열재에는 여러 종류가 있지만 주로 사용되는 것으로는 압출법 보온판, 비드법 보온판...  
4    도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수 있습니다. 건조 기간 ...  
..                                                 ...  
125  분말 소화기를 사용할 때 주의할 점은 몇 가지가 있습니다. 압력계의 눈금 위치가 초...  
126  압출법 단열판은 습기에 강하고, 곰팡이 및 세균의 증식을 방지하기 때문에 실내 환경...  
127  수성 벽체용 탄성 방수 도료는 치밀한 표면구성과 탄성 있는 도막을 형성하여 우수한 ...  
128  석고수정이란 벽을 이루는 석고에 훼손이 발생한 상태를 말합니다. 보편적인 원인으로는...  
129  카페트의 기대수명은 보통 6년입니다. 그러나 이는 카페트의 사용빈도, 관리방법, 카...  

[130 rows x 3 columns]

In [45]:
valid = pd.read_csv(f'{DATA_PATH}valid.csv')
valid_sim = pd.read_csv(f'{DATA_PATH}valid_sim.csv')

test = pd.read_csv(f'{DATA_PATH}test.csv')
train_ft = pd.read_csv(f'{DATA_PATH}category_train_120000_ver4.csv')

test_qna_cat = pd.read_csv(f'{DATA_PATH}test_qna_cat.csv')
test_sim = pd.read_csv(f'{DATA_PATH}test_sim2.csv')
test_sim2 = pd.read_csv(f'{DATA_PATH}test_sim3.csv')


valid_qna_cat = pd.read_csv(f'{DATA_PATH}valid_sim_qna_cat.csv')

train_ft.head()
test

id                                                 질문
0    TEST_000  방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용...
1    TEST_001            도배지에 녹은 자국이 발생하는 주된 원인과 그 해결 방법은 무엇인가요?
2    TEST_002    큐블럭의 단점을 알려주세요. 또한, 압출법 단열판을 사용하는 것의 장점은 무엇인가요?
3    TEST_003  철골구조를 사용하는 고층 건물에서, 단열 효과를 높이기 위한 시공 방법은 무엇이 있...
4    TEST_004                   도배지의 완전한 건조를 위해 몇 주 동안 기다려야 하나요?
..        ...                                                ...
125  TEST_125  분말 소화기를 사용할 때 주의해야 할 사항은 무엇인가요? 그리고 아파트 도배 평수를...
126  TEST_126                          압출법 보온판의 가장 큰 장점은 무엇인가요?"
127  TEST_127  평지붕의 누수 문제를 방지하기 위해 수성 벽체용 탄성 방수 도료를 사용하는 것이 어...
128  TEST_128  석고수정이 발생하는 가장 큰 원인은 무엇인가요? 그리고 이를 해결하는 방법에 대해 ...
129  TEST_129     카페트의 기대 수명은 얼마나 될까요? 그리고 오리지널징크의 장점에는 무엇이 있나요?

[130 rows x 2 columns]

In [8]:
test = pd.read_csv(f'{DATA_PATH}valid_sim.csv')
test

질문  \
0                                 테라죠의 평균 수명은 몇 년인가요?   
1                                  플로킹 벽지란 무엇을 의미하나요?   
2                                건조는 며칠 동안 진행되어야 하나요?   
3                                        장판의 장점이 뭔가요?   
4                                   도막방수공사는 어떤 작업인가요?   
..                                                ...   
95         발수공사란 무엇을 무엇이고, 천연 재료로 만들어진 벽지에 대해 설명해주세요.   
96  도배 작업에는 몇 명이 필요한가요? 그리고 마루에 생긴 스크래치를 숨길 방법이 있을까요?   
97  마루의 장점은 무엇인가요? 또한, 낡은 목재 가구에 있는 흠집을 감춰주는 방법을 알...   
98    속건형 유성 발수제란 무엇인지 무엇이고, 면진과 제진의 구조에는 어떤 차이가 있나요?   
99  왜 천장에서 물이 새나요? 또한, 모던한 스타일로 거실을 꾸미는 방법에 대해 알려주세요.   

                                                 답변_1  \
0                                  테라죠의 기대수명은 30년입니다.   
1   벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트...   
2            도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수도 있습니다.   
3   장판은 단가와 시공비가 저렴하고 보행감이 좋으며 높은 열전도율로 난방효과가 좋고 층...   
4   도막방수는 방수용으로 제조된 우레탄 고무계, 아크릴 고무계, 고무 아스팔트계 등의 ...   
..                                                ...   
95  발수공사란 콘크리트 구체 및 모르타르, 벽돌 벽체 등 흡수성을 갖는 바탕재에 고분자...   
96  일반적으로 30평 아파트 기준 도배에 필요한 인원은 합지벽지는 3명의 도배사, 실크...   
97  마루는 나무본연의 부드러운 촉감과 질감을 느낄 수 있다는 장점이 있습니다. 또한, ...   
98  속건형 유성 발수제는 유성계 발수제로서 도장 후 용제가 증발되면서 발수효과를 발휘하...   
99  천장의 물을 그릇으로 모아 물이 새는 원인을 확인하고 누수를 막는 조치를 취하세요....   

                                                유사_답변  \
0                                  테라죠의 기대수명은 30년입니다.   
1   벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트...   
2            도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수도 있습니다.   
3   장판은 단가와 시공비가 저렴하고 보행감이 좋으며 높은 열전도율로 난방효과가 좋고 층...   
4   도막방수는 방수용으로 제조된 우레탄 고무계, 아크릴 고무계, 고무 아스팔트계 등의 ...   
..                                                ...   
95  발수공사란 콘크리트 구체 및 모르타르, 벽돌 벽체 등 흡수성을 갖는 바탕재에 고분자...   
96  일반적으로 30평 아파트 기준 도배에 필요한 인원은 합지벽지는 3명의 도배사, 실크...   
97  마루는 나무본연의 부드러운 촉감과 질감을 느낄 수 있다는 장점이 있습니다. 흠집을 ...   
98  속건형 유성 발수제는 유성계 발수제로서 도장 후 용제가 증발되면서 발수효과를 발휘하...   
99  천장의 물을 그릇으로 모아 물이 새는 원인을 확인하고 누수를 막는 조치를 취하세요....   

                                         유사도  
0                       [0.9864692687988281]  
1                       [0.9820297360420227]  
2                       [0.8654287457466125]  
3                       [0.9892034530639648]  
4                       [0.9870628714561462]  
..                                       ...  
95   [0.9544162750244141, 0.785067617893219]  
96  [0.9608222842216492, 0.9883949756622314]  
97   [0.9999998211860657, 0.914232075214386]  
98  [0.9676459431648254, 0.7238320112228394]  
99  [0.9663888216018677, 0.8691998720169067]  

[100 rows x 4 columns]

In [9]:
def cosine_similarity(a, b):
    dot_product = np.dot(a, b)
    norm_a = np.linalg.norm(a)
    norm_b = np.linalg.norm(b)
    return dot_product / (norm_a * norm_b) if norm_a != 0 and norm_b != 0 else 0

In [10]:
from sklearn.metrics.pairwise import pairwise_distances
embedding_model = SentenceTransformer('distiluse-base-multilingual-cased-v1')

def cosine_score(input_text, generated_text):
    input_embedding = embedding_model.encode(input_text)
    generated_embedding = embedding_model.encode(generated_text)

    cosine_similarity_score = cosine_similarity(input_embedding, generated_embedding)
    cosine_similarity_score = max(cosine_similarity_score, 0)

    return cosine_similarity_score

def evaluate_similarity(input_text, generated_text, alpha=0.95): # cosine 가중치 조절
    input_embedding = embedding_model.encode(input_text)
    generated_embedding = embedding_model.encode(generated_text)

    # 코사인 유사도
    cosine_sim = 1 - pairwise_distances([input_embedding], [generated_embedding], metric='cosine')[0][0]

    # 자카드 유사도
    input_tokens = set(input_text.split())
    generated_tokens = set(generated_text.split())
    jaccard_sim = len(input_tokens.intersection(generated_tokens)) / len(input_tokens.union(generated_tokens))

    # 가중 평균 내보기
    weighted_sim = alpha*cosine_sim + (1 - alpha)*jaccard_sim

    return weighted_sim

/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:88: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


modules.json:   0%|          | 0.00/341 [00:00<?, ?B/s]

config_sentence_transformers.json:   0%|          | 0.00/122 [00:00<?, ?B/s]

README.md:   0%|          | 0.00/2.47k [00:00<?, ?B/s]

sentence_bert_config.json:   0%|          | 0.00/53.0 [00:00<?, ?B/s]

...

tokenizer.json:   0%|          | 0.00/1.96M [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/112 [00:00<?, ?B/s]

1_Pooling/config.json:   0%|          | 0.00/190 [00:00<?, ?B/s]

2_Dense/config.json:   0%|          | 0.00/114 [00:00<?, ?B/s]

pytorch_model.bin:   0%|          | 0.00/1.58M [00:00<?, ?B/s]

In [11]:
!pip install kiwipiepy

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.8/2.8 MB 9.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 34.7/34.7 MB 10.2 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
  Created wheel for kiwipiepy-model: filename=kiwipiepy_model-0.17.0-py3-none-any.whl size=34845034 sha256=131707cb32e7bc544259bdfa97db568c395b0a37f8ae9eed271cd22606fc70fd
  Stored in directory: /root/.cache/pip/wheels/90/bb/ae/15e1cf26d17183040bac268fbf8d1ca1f45f7f4daa0fb76b91
Successfully built kiwipiepy-model


In [12]:
from kiwipiepy import Kiwi

kiwi = Kiwi()
kiwi.tokenize(train_ft['question'][0])

[Token(form='면', tag='NNG', start=0, len=1),
 Token(form='지', tag='VV', start=1, len=1),
 Token(form='ᆫ', tag='ETM', start=1, len=1),
 Token(form='장치', tag='NNG', start=2, len=2),
 Token(form='가', tag='JKS', start=4, len=1),
 Token(form='뭐', tag='NP', start=6, len=1),
 Token(form='이', tag='VCP', start=7, len=0),
 Token(form='야', tag='EF', start=7, len=1),
 Token(form='?', tag='SF', start=8, len=1)]

In [13]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import pairwise_distances
embedding_model = SentenceTransformer('distiluse-base-multilingual-cased-v1')

def get_kiwi_nouns(text):
    pos_result = kiwi.tokenize(text)
    nouns = [word for word, pos, _,_ in pos_result if pos.startswith('N')]
    return ' '.join(nouns)

def kiwi_evaluate_similarity(input_text, generated_text, alpha=0.95): # cosine 가중치 조절

    input_embedding = embedding_model.encode(get_kiwi_nouns(input_text))
    generated_embedding = embedding_model.encode(get_kiwi_nouns(generated_text))

    # 코사인 유사도
    cosine_sim = 1 - pairwise_distances([input_embedding], [generated_embedding], metric='cosine')[0][0]

    # 자카드 유사도
    input_tokens = set(input_text.split())
    generated_tokens = set(generated_text.split())
    jaccard_sim = len(input_tokens.intersection(generated_tokens)) / len(input_tokens.union(generated_tokens))

    # 가중 평균 내보기
    weighted_sim = alpha*cosine_sim + (1 - alpha)*jaccard_sim

    return weighted_sim

In [20]:
def cosine_score(input_text, generated_text): # cosine 가중치 조절
    input_embedding = embedding_model.encode(input_text)
    generated_embedding = embedding_model.encode(generated_text)

    # 코사인 유사도
    cosine_sim = 1 - pairwise_distances([input_embedding], [generated_embedding], metric='cosine')[0][0]

    return cosine_sim

# 후처리

In [27]:

def post_processing(text):
    import re
    end = text.rfind('</s>')
    if end:
        text = text[:end]

    end = text.rfind('.')
    text = text[:end+1]

    text = text.strip()
    text = text.replace('\n', '').replace('<unk>','').replace('*','')
    text = re.sub(' +', ' ', text)
    return text



In [28]:
text = '   온돌마루의 수명은 얼마나 될까요?. 그리고. 문이</s> 정확히 열리지 <unk>거나 닫히지 않을 때는 어떻게 대처해야 하나요.? 왜냐하면 그게 그렇</s>'

post_processing(text)

'온돌마루의 수명은 얼마나 될까요?. 그리고. 문이</s> 정확히 열리지 거나 닫히지 않을 때는 어떻게 대처해야 하나요.'

# 모델 추론

In [16]:
# from transformers import GPT2LMHeadModel

# model_name = 'skt/kogpt2-base-v2'
# finetune_model = 'kogpt2_qnacat_120000_3epoch_0.19047loss'


# model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{finetune_model}').to(device)
# tokenizer = AutoTokenizer.from_pretrained(model_name,
#                                                     bos_token='</s>',
#                                                     eos_token='</s>',
#                                                     unk_token='<unk>',
#                                                     pad_token='<pad>',
#                                                     mask_token='<mask>')

KeyboardInterrupt: 

# VALID 모델 추론 -1 (No qna_cat)

In [29]:
def valid_sim_Chatbot(input_text, similar_text, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    similar_text = similar_text.strip()
    text = '<q>' + input_text + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len:])

        similarity_score = evaluate_similarity(similar_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

## epoch 3 : 0.9093387657403946

In [22]:
model_name = 'kogpt2_qnacat_120000_3epoch_0.19047loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')

mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    answer, score = valid_sim_Chatbot(text, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

KeyboardInterrupt: 

## epoch 4 : 0.9185110026597977

In [30]:
model_name = 'kogpt2_qnacat_120000_4epoch_0.16569loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')

mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    answer, score = valid_sim_Chatbot(text, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.5531090250140741, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(0.9447387582063674, '테라죠는 기대수명이 30년입니다.')
(0.9447387582063674, '테라죠는 기대수명이 30년입니다.')
(0.4902019135378025, '테라죠의 평균 수명은 30년입니다. 그러나 올바른 유지보수와 적절한 사용 조건이 갖추어진다면 더 오래 사용할 수 있습니다. 유지보수는 특히 중요한데, 특히 사용 환경과 노출 정도에 따라 이 기간이 달라질 수 있습니다.')
(0.617378911605248, '테라죠의 평균 수명은 30년입니다.30년이라는 수명은 테라죠의 내구성과 사용 환경에 따라 다를 수 있습니다.')
테라죠는 기대수명이 30년입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.7102733969688415, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 이는 고급스러운 분위기를 연출하며 포인트 용으로 적합합니다. 그러나, 플로킹 벽지는 가격이 비싸고 내구성이 떨어지며 관리가 어렵다는 단점이 있습니다. 특히, 습기에 민감하며 세척이 어렵기 때문에 주의가 필요합니다.')
(0.9999999433755875, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다.')
(0.7102733969688415, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 이는 고급스러운 분위기를 연출하며 포인트 용으로 적합합니다. 그러나, 플로킹 벽지는 가격이 비싸고 내구성이 떨어지며 관리가 어렵다는 단점이 있습니

## epoch 5 : 0.8964872866868973

In [31]:
model_name = 'kogpt2_qnacat_120000_5epoch_0.15203loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')

mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    answer, score = valid_sim_Chatbot(text, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.4662690305047565, '테라죠는 일반적으로 30년 정도 사용 가능한 것으로 알려져 있습니다. 그러나 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명은 다를 수 있습니다. 따라서 테라죠의 수명을 늘리기 위해서는 제조사의 권장 사례를 따르는 것이 좋습니다.')
(0.5787452773915397, '테라죠의 예상 수명은 일반적으로 30년입니다. 그러나 올바른 유지보수와 적절한 사용 조건이 갖추어진다면 더 오래 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달라질 수 있습니다. 유지보수는 매우 중요하며, 적절하게 이루어지면 테라죠의 수명을 연장하는 데 도움이 됩니다.')
(0.5986543926170894, '테라죠의 기대수명은 일반적으로 30년입니다. 그러나 올바른 유지보수와 적절한 사용 조건이 갖추어진다면 더 오랜 시간 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달라질 수 있습니다. 유지보수는 매우 중요하며, 적절하게 이루어지면 테라죠의 수명을 연장하는 데 도움이 됩니다.')
(0.4662690305047565, '테라죠는 일반적으로 30년 정도 사용 가능한 것으로 알려져 있습니다. 그러나 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명은 다를 수 있습니다. 따라서 테라죠의 수명을 늘리기 위해서는 제조사의 권장 사례를 따르는 것이 좋습니다.')
(0.4662690305047565, '테라죠는 일반적으로 30년 정도 사용 가능한 것으로 알려져 있습니다. 그러나 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명은 다를 수 있습니다. 따라서 테라죠의 수명을 늘리기 위해서는 제조사의 권장 사례를 따르는 것이 좋습니다.')
테라죠의 기대수명은 일반적으로 30년입니다. 그러나 올바른 유지보수와 적절한 사용 조건이 갖추어진다면 더 오랜 시간 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달

## epoch 6 : 0.902074014544487

In [32]:
model_name = 'kogpt2_qnacat_120000_6epoch_0.14374loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')

mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    answer, score = valid_sim_Chatbot(text, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.5534668239263387, '테라죠의 기대수명은 일반적으로 30년이며, 이는 우수한 품질의 테라죠 제품을 제대로 유지보수하고 적절히 관리했을 경우의 수명입니다. 올바른 관리와 유지보수가 이루어지면 테라죠 바닥은 오랫동안 사용할 수 있을 것입니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
테라죠의 기대수명은 30년입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.7216686547529406, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지로, 고급스러운 분위기를 연출하며 포인트 용으로 적합합니다. 그러나 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다. 또한, 플로킹 벽지를 청소할 때는 높은 주의가 필요하며, 습기에 노출되면 벨벳 소재가 손상될 수 있으므로 주의가 필요합니다.')
(0.7216686547529406, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지로, 고급스러운 분위기를 연출하며 포인트 용으로 적합합니다. 그러나 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다. 또한, 플로킹 벽지를 청소할 때는 높은 주의가 필요하며, 습기에 노출되면 벨벳 소재가 손상될 수 있으므로 주의가 필요합니다.')
(0.7216686547529406, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지로, 고급스러운 분위기를 연출하며 포인트 용으로 적합합니다. 그러나 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다. 또한, 플로킹 벽지를 청소할 때는 높은 주의가 필요하며, 습기에 노출되면 벨벳 소재가 손상될 수 있으므로 주의가 필요합니다.')
(0.7216686547529406, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지로, 고급스러운 분위기를 연출하며 포인트 용으로 적합합니다. 

## epoch 7 :

In [33]:
model_name = 'kogpt2_qnacat_120000_7epoch_0.13839loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')

mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    answer, score = valid_sim_Chatbot(text, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.4662690305047565, '테라죠는 일반적으로 30년 정도 사용 가능한 것으로 알려져 있습니다. 그러나 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명은 다를 수 있습니다. 따라서 테라죠의 수명을 늘리기 위해서는 제조사의 권장 사례를 따르는 것이 좋습니다.')
(0.601714615867688, '테라죠의 기대수명은 일반적으로 30년입니다. 이는 테라죠의 내구성과 사용 환경에 따라 다를 수 있으므로, 지속적인 유지보수와 적절한 사용 환경 조성이 중요합니다. 또한, 테라죠의 수명을 연장시키기 위해서는 정기적인 청소와 보수가 필요합니다.')
(-0.01084255576133728, '')
(0.601714615867688, '테라죠의 기대수명은 일반적으로 30년입니다. 이는 테라죠의 내구성과 사용 환경에 따라 다를 수 있으므로, 지속적인 유지보수와 적절한 사용 환경 조성이 중요합니다. 또한, 테라죠의 수명을 연장시키기 위해서는 정기적인 청소와 보수가 필요합니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
테라죠의 기대수명은 30년입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.6659439486265183, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 이러한 벽지는 고급스러운 분위기를 연출하며, 주로 포인트 용으로 사용되는데 가격이 비싸고 내구성이 떨어지며 유지보수가 어렵다는 단점이 있습니다. 이러한 특징으로 플로킹 벽지는 디자인적인 면에서는 매력적이지만, 유지보수와 내구성 측면에서 신중하게 선택해야 합니다.')
(0.7102733969688415, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 이는 고급스러운 분위기를 연출하며 포인트 용으로 적합합니다. 그러나, 플로킹 벽지는 가격이 비싸고 내구성이 떨어지며 관리가 어렵다는 단점이 있습니다. 특히, 습기에 민감하며 세척이 어렵기 때문에 주의가 필요합니다.')
(0.7102733969688415,

KeyboardInterrupt: 

In [46]:
test_qna_cat = pd.read_csv(f'{DATA_PATH}test_qna_cat.csv')
test_sim = pd.read_csv(f'{DATA_PATH}test_sim2.csv')
valid_qna_cat = test_qna_cat = pd.read_csv(f'{DATA_PATH}valid_sim_qna_cat.csv')


# VALID 모델 추론 -2 (Yes qna_cat)

In [ ]:
valid_qna = valid_qna_cat['qna_category'].tolist()

In [56]:
def QnA_valid_sim_Chatbot(input_text, input_qna, similar_text, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    similar_text = similar_text.strip()
    text = '<q>' + input_text + '</s><t>' + input_qna + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len+1:])

        similarity_score = evaluate_similarity(similar_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

In [53]:
valid_sim['qna_category'] = valid_qna
valid_sim

질문  \
0                                 테라죠의 평균 수명은 몇 년인가요?   
1                                  플로킹 벽지란 무엇을 의미하나요?   
2                                건조는 며칠 동안 진행되어야 하나요?   
3                                        장판의 장점이 뭔가요?   
4                                   도막방수공사는 어떤 작업인가요?   
..                                                ...   
95         발수공사란 무엇을 무엇이고, 천연 재료로 만들어진 벽지에 대해 설명해주세요.   
96  도배 작업에는 몇 명이 필요한가요? 그리고 마루에 생긴 스크래치를 숨길 방법이 있을까요?   
97  마루의 장점은 무엇인가요? 또한, 낡은 목재 가구에 있는 흠집을 감춰주는 방법을 알...   
98    속건형 유성 발수제란 무엇인지 무엇이고, 면진과 제진의 구조에는 어떤 차이가 있나요?   
99  왜 천장에서 물이 새나요? 또한, 모던한 스타일로 거실을 꾸미는 방법에 대해 알려주세요.   

                                                 답변_1  \
0                                  테라죠의 기대수명은 30년입니다.   
1   벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트...   
2            도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수도 있습니다.   
3   장판은 단가와 시공비가 저렴하고 보행감이 좋으며 높은 열전도율로 난방효과가 좋고 층...   
4   도막방수는 방수용으로 제조된 우레탄 고무계, 아크릴 고무계, 고무 아스팔트계 등의 ...   
..                                                ...   
95  발수공사란 콘크리트 구체 및 모르타르, 벽돌 벽체 등 흡수성을 갖는 바탕재에 고분자...   
96  일반적으로 30평 아파트 기준 도배에 필요한 인원은 합지벽지는 3명의 도배사, 실크...   
97  마루는 나무본연의 부드러운 촉감과 질감을 느낄 수 있다는 장점이 있습니다. 또한, ...   
98  속건형 유성 발수제는 유성계 발수제로서 도장 후 용제가 증발되면서 발수효과를 발휘하...   
99  천장의 물을 그릇으로 모아 물이 새는 원인을 확인하고 누수를 막는 조치를 취하세요....   

                                                유사_답변  \
0                                  테라죠의 기대수명은 30년입니다.   
1   벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트...   
2            도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수도 있습니다.   
3   장판은 단가와 시공비가 저렴하고 보행감이 좋으며 높은 열전도율로 난방효과가 좋고 층...   
4   도막방수는 방수용으로 제조된 우레탄 고무계, 아크릴 고무계, 고무 아스팔트계 등의 ...   
..                                                ...   
95  발수공사란 콘크리트 구체 및 모르타르, 벽돌 벽체 등 흡수성을 갖는 바탕재에 고분자...   
96  일반적으로 30평 아파트 기준 도배에 필요한 인원은 합지벽지는 3명의 도배사, 실크...   
97  마루는 나무본연의 부드러운 촉감과 질감을 느낄 수 있다는 장점이 있습니다. 흠집을 ...   
98  속건형 유성 발수제는 유성계 발수제로서 도장 후 용제가 증발되면서 발수효과를 발휘하...   
99  천장의 물을 그릇으로 모아 물이 새는 원인을 확인하고 누수를 막는 조치를 취하세요....   

                                         유사도        qna_category  
0                       [0.9864692687988281]           ['수명.주기']  
1                       [0.9820297360420227]              ['설명']  
2                       [0.8654287457466125]                  []  
3                       [0.9892034530639648]              ['장점']  
4                       [0.9870628714561462]                  []  
..                                       ...                 ...  
95   [0.9544162750244141, 0.785067617893219]              ['설명']  
96  [0.9608222842216492, 0.9883949756622314]           ['방법.대책']  
97   [0.9999998211860657, 0.914232075214386]     ['장점', '방법.대책']  
98  [0.9676459431648254, 0.7238320112228394]     ['설명', '차이.비교']  
99  [0.9663888216018677, 0.8691998720169067]  ['방법.대책', '원인.이유']  

[100 rows x 5 columns]

## epoch 3 - 기준 : 0.9080921185016632

In [57]:
model_name = 'kogpt2_qnacat_120000_3epoch_0.19047loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')

mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = QnA_valid_sim_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.47854015827178953, '테라죠는 일반적으로 30년 동안 사용할 수 있는 것으로 알려져 있습니다. 그러나 적절한 유지보수와 사용 환경 조건을 제공할 경우, 더 오래 사용할 수도 있습니다. 하지만 제품의 품질과 사용 방법에 따라 사용 가능 여부가 달라질 수 있으므로 주의가 필요합니다.')
(0.6187497553825378, '테라죠의 기대수명은 일반적으로 30년입니다. 그러나 올바른 유지보수와 적절한 사용 환경 조건을 유지하면 더 오랜 수명을 기대할 수 있습니다. 따라서 테라죠를 정기적으로 점검하고 보수하는 것이 중요합니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
(0.5590080430633143, '테라죠는 일반적으로 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리기 위해서는 제조사의 권장 사례를 따르는 것이 좋습니다.')
테라죠의 기대수명은 30년입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.9999999433755875, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다.')
(0.7122567574183146, '벨벳 소재로 만들어진 플로킹 벽지는 입체적인 느낌을 주어 고급스러움을 더합니다. 이는 포인트로 사용하기에 아주 적합하며, 인테리어를 더욱 돋보이게 해줍니다. 하지만 그만큼 가격이 비싸고 내구성도 다소 낮으며 유지보수도 어렵다는 단점이 있습니다. 특히 청소 시에는 주의가 필요하며, 습기에 노출되면 소재가 손상될 수 있으므로 조심해야 합니다.')
(0.9999999433755875, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운

## epoch 4 : category + qna 0.9134007376432419

In [115]:
model_name = 'kogpt2_qnacat_120000_4epoch_0.15230loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')


mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = QnA_valid_sim_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.5531090250140741, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(0.46456507750919884, '테라죠는 정확한 유지보수와 적절한 관리가 이루어진다면, 일반적으로 30년 동안 사용할 수 있다고 기대됩니다. 그러나 테라죠의 수명을 늘리기 위해서는 제조사의 권장 사례를 따르는 것이 좋습니다. 따라서 테라죠 제품을 잘 관리하고 유지보수한다면 테라죠의 수명을 최대한으로 연장할 수 있습니다.')
(0.47658383706036733, '테라죠는 정확한 유지보수와 적절한 관리가 이루어진 경우에는 일반적으로 30년 동안 사용할 수 있다고 예상됩니다. 그러나 테라죠의 수명은 사용 환경과 유지보수 여부에 따라 다를 수 있습니다. 지속적인 관리와 보수가 이루어지면 테라죠는 오랫동안 사용할 수 있는 것으로 알려져 있습니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
(0.5086884587100058, '테라죠의 평균 수명은 30년입니다. 그러나 올바른 유지보수와 올바른 사용 조건이 갖추어진다면 더 오랜 시간 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달라질 수 있습니다. 유지보수는 매우 중요하며, 적절하게 이루어지면 테라죠의 수명을 최대한으로 연장할 수 있습니다.')
테라죠의 기대수명은 30년입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.6659439486265183, '플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 이러한 벽지는 고급스러운 분위기를 연출하며, 주로 포인트 용으로 사용되는데 가격이 비싸고 내구성이 떨어지며 유지보수가 어렵다는 단점이 있습니다. 이러한 특징으로 플로킹 벽지는 디자인적인 면에서는 매력적이지만,

## epoch 4 : 0.9224619817733765 ****

In [59]:
model_name = 'kogpt2_qnacat_120000_4epoch_0.16569loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')


mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = QnA_valid_sim_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.5531090250140741, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(0.5716274082660675, '테라죠는 기대수명이 30년인 것으로 알려져 있습니다. 이는 우수한 품질의 테라죠 제품을 제대로 유지보수하고 적절히 관리했을 경우의 수명입니다. 올바른 관리와 유지보수가 이루어지면 테라죠 바닥은 오랫동안 사용할 수 있을 것입니다.')
(0.5531090250140741, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
(1.0, '테라죠의 기대수명은 30년입니다.')
테라죠의 기대수명은 30년입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.9999999433755875, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다.')
(0.9999999433755875, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다.')
(0.9999999433755875, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이

## epoch 4 : 답변 2와 유사도

In [111]:
valid_qna = valid_qna_cat['qna_category'].tolist()

In [113]:
valid_qna_cat

question  \
0                                 테라죠의 평균 수명은 몇 년인가요?   
1                                  플로킹 벽지란 무엇을 의미하나요?   
2                                건조는 며칠 동안 진행되어야 하나요?   
3                                        장판의 장점이 뭔가요?   
4                                   도막방수공사는 어떤 작업인가요?   
..                                                ...   
95         발수공사란 무엇을 무엇이고, 천연 재료로 만들어진 벽지에 대해 설명해주세요.   
96  도배 작업에는 몇 명이 필요한가요? 그리고 마루에 생긴 스크래치를 숨길 방법이 있을까요?   
97  마루의 장점은 무엇인가요? 또한, 낡은 목재 가구에 있는 흠집을 감춰주는 방법을 알...   
98    속건형 유성 발수제란 무엇인지 무엇이고, 면진과 제진의 구조에는 어떤 차이가 있나요?   
99  왜 천장에서 물이 새나요? 또한, 모던한 스타일로 거실을 꾸미는 방법에 대해 알려주세요.   

                                                 답변_1  \
0                                  테라죠의 기대수명은 30년입니다.   
1   벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트...   
2            도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수도 있습니다.   
3   장판은 단가와 시공비가 저렴하고 보행감이 좋으며 높은 열전도율로 난방효과가 좋고 층...   
4   도막방수는 방수용으로 제조된 우레탄 고무계, 아크릴 고무계, 고무 아스팔트계 등의 ...   
..                                                ...   
95  발수공사란 콘크리트 구체 및 모르타르, 벽돌 벽체 등 흡수성을 갖는 바탕재에 고분자...   
96  일반적으로 30평 아파트 기준 도배에 필요한 인원은 합지벽지는 3명의 도배사, 실크...   
97  마루는 나무본연의 부드러운 촉감과 질감을 느낄 수 있다는 장점이 있습니다. 또한, ...   
98  속건형 유성 발수제는 유성계 발수제로서 도장 후 용제가 증발되면서 발수효과를 발휘하...   
99  천장의 물을 그릇으로 모아 물이 새는 원인을 확인하고 누수를 막는 조치를 취하세요....   

                                                유사_답변  \
0                                  테라죠의 기대수명은 30년입니다.   
1   벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트...   
2            도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수도 있습니다.   
3   장판은 단가와 시공비가 저렴하고 보행감이 좋으며 높은 열전도율로 난방효과가 좋고 층...   
4   도막방수는 방수용으로 제조된 우레탄 고무계, 아크릴 고무계, 고무 아스팔트계 등의 ...   
..                                                ...   
95  발수공사란 콘크리트 구체 및 모르타르, 벽돌 벽체 등 흡수성을 갖는 바탕재에 고분자...   
96  일반적으로 30평 아파트 기준 도배에 필요한 인원은 합지벽지는 3명의 도배사, 실크...   
97  마루는 나무본연의 부드러운 촉감과 질감을 느낄 수 있다는 장점이 있습니다. 흠집을 ...   
98  속건형 유성 발수제는 유성계 발수제로서 도장 후 용제가 증발되면서 발수효과를 발휘하...   
99  천장의 물을 그릇으로 모아 물이 새는 원인을 확인하고 누수를 막는 조치를 취하세요....   

                                         유사도        qna_category  
0                       [0.9864692687988281]           ['수명.주기']  
1                       [0.9820297360420227]              ['설명']  
2                       [0.8654287457466125]                  []  
3                       [0.9892034530639648]              ['장점']  
4                       [0.9870628714561462]                  []  
..                                       ...                 ...  
95   [0.9544162750244141, 0.785067617893219]              ['설명']  
96  [0.9608222842216492, 0.9883949756622314]           ['방법.대책']  
97   [0.9999998211860657, 0.914232075214386]     ['장점', '방법.대책']  
98  [0.9676459431648254, 0.7238320112228394]     ['설명', '차이.비교']  
99  [0.9663888216018677, 0.8691998720169067]  ['방법.대책', '원인.이유']  

[100 rows x 5 columns]

In [119]:
valid_sim2

id                                                 질문  \
0    TEST_000  방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용...   
1    TEST_001            도배지에 녹은 자국이 발생하는 주된 원인과 그 해결 방법은 무엇인가요?   
2    TEST_002    큐블럭의 단점을 알려주세요. 또한, 압출법 단열판을 사용하는 것의 장점은 무엇인가요?   
3    TEST_003  철골구조를 사용하는 고층 건물에서, 단열 효과를 높이기 위한 시공 방법은 무엇이 있...   
4    TEST_004                   도배지의 완전한 건조를 위해 몇 주 동안 기다려야 하나요?   
..        ...                                                ...   
125  TEST_125  분말 소화기를 사용할 때 주의해야 할 사항은 무엇인가요? 그리고 아파트 도배 평수를...   
126  TEST_126                           압출법 보온판의 가장 큰 장점은 무엇인가요?   
127  TEST_127  평지붕의 누수 문제를 방지하기 위해 수성 벽체용 탄성 방수 도료를 사용하는 것이 어...   
128  TEST_128  석고수정이 발생하는 가장 큰 원인은 무엇인가요? 그리고 이를 해결하는 방법에 대해 ...   
129  TEST_129     카페트의 기대 수명은 얼마나 될까요? 그리고 오리지널징크의 장점에는 무엇이 있나요?   

                                                 유사_답변  
0    방청 페인트는 다양한 종류로 분류됩니다. 그 종류에는 광명단 페인트, 방청산화철 페...  
1    도배지에 녹이 묻어나오는 것은 녹오염으로, 도배지 상에 녹색 또는 갈색의 녹이 발생...  
2    큐블럭은 일반 벽돌에 비해 높은 비용과 균열이 쉽게 생길 수 있는 점, 그리고 습기...  
3    단열재에는 여러 종류가 있지만 주로 사용되는 것으로는 압출법 보온판, 비드법 보온판...  
4    도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수 있습니다. 건조 기간 ...  
..                                                 ...  
125  분말 소화기를 사용할 때 주의할 점은 몇 가지가 있습니다. 압력계의 눈금 위치가 초...  
126  압출법 단열판은 습기에 강하고, 곰팡이 및 세균의 증식을 방지하기 때문에 실내 환경...  
127  수성 벽체용 탄성 방수 도료는 치밀한 표면구성과 탄성 있는 도막을 형성하여 우수한 ...  
128  석고수정이란 벽을 이루는 석고에 훼손이 발생한 상태를 말합니다. 보편적인 원인으로는...  
129  카페트의 기대수명은 보통 6년입니다. 그러나 이는 카페트의 사용빈도, 관리방법, 카...  

[130 rows x 3 columns]

In [120]:
valid_sim2 = pd.read_csv(f'{DATA_PATH}valid_sim2.csv')
valid_sim2['qna_category'] = valid_qna
valid_sim2

질문  \
0                               테라죠의 평균 수명은 몇 년인가요?   
1                                플로킹 벽지란 무엇을 의미하나요?   
2                              건조는 며칠 동안 진행되어야 하나요?   
3                                      장판의 장점이 뭔가요?   
4                                 도막방수공사는 어떤 작업인가요?   
..                                              ...   
95       발수공사란 무엇을 무엇이고, 천연 재료로 만들어진 벽지에 대해 설명해주세요.   
96    도배 작업에는 몇 명이 필요한가요? 마루에 생긴 스크래치를 숨길 방법이 있을까요?   
97  마루의 장점은 무엇인가요? 낡은 목재 가구에 있는 흠집을 감춰주는 방법을 알려주세요.   
98  속건형 유성 발수제란 무엇인지 무엇이고, 면진과 제진의 구조에는 어떤 차이가 있나요?   
99    왜 천장에서 물이 새나요? 모던한 스타일로 거실을 꾸미는 방법에 대해 알려주세요.   

                                                유사_답변        qna_category  
0   테라죠의 기대수명은 일반적으로 30년이며, 이는 우수한 품질의 테라죠 제품을 제대로...           ['수명.주기']  
1   플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 이는 고급스러운 분위...              ['설명']  
2   도배 후 도배지가 완전히 건조되기까지 최대 일주일이 걸릴 수 있습니다. 건조 기간 ...                  []  
3   장판은 단가와 시공비가 저렴하여 비용 효율적이며 보행감이 좋아 편안한 걷기가 가능합...              ['장점']  
4   도막방수는 건물의 지붕, 벽, 바닥과 같은 부분에 방수용으로 제조된 우레탄 고무계,...                  []  
..                                                ...                 ...  
95  발수공사는 콘크리트 구조물, 벽돌 벽체 등과 같이 흡수성이 있는 바탕재에 고분자 유...              ['설명']  
96  도배 작업에 필요한 인원은 주로 평수와 사용하는 도배재의 종류에 따라 다를 수 있습...           ['방법.대책']  
97  흠집을 가릴 때 목재 펜스틱을 사용해 채우고, 이후에 같은 색상의 나무 왁스로 마무...     ['장점', '방법.대책']  
98  속건형 유성 발수제는 유성계 발수제로서 도장 후 용제가 증발되면서 발수효과를 발휘하...     ['설명', '차이.비교']  
99  현대적인 거실을 꾸미기 위해서는 먼저 미니멀한 디자인과 현대적인 가구, 그리고 간결...  ['방법.대책', '원인.이유']  

[100 rows x 3 columns]

In [121]:
model_name = 'kogpt2_qnacat_120000_4epoch_0.16569loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')


mean_score = []
answer_list = []
for _, row in tqdm(valid_sim2.iterrows(), total=valid_sim2.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = QnA_valid_sim_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim2['유사_답변'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.7559224874808871, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(0.9522871161660841, '테라죠는 기대수명이 30년인 것으로 알려져 있습니다. 이는 우수한 품질의 테라죠 제품을 제대로 유지보수하고 적절히 관리했을 경우의 수명입니다. 올바른 관리와 유지보수가 이루어지면 테라죠 바닥은 오랫동안 사용할 수 있을 것입니다.')
(0.7559224874808871, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(0.5534668239263387, '테라죠의 기대수명은 30년입니다.')
(0.5534668239263387, '테라죠의 기대수명은 30년입니다.')
테라죠는 기대수명이 30년인 것으로 알려져 있습니다. 이는 우수한 품질의 테라죠 제품을 제대로 유지보수하고 적절히 관리했을 경우의 수명입니다. 올바른 관리와 유지보수가 이루어지면 테라죠 바닥은 오랫동안 사용할 수 있을 것입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.7102733969688415, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다.')
(0.7102733969688415, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며

## epoch 4 : Kiwi 유사도 0.9212215673923493

In [92]:
def Kiwi_QnA_valid_sim_Chatbot(input_text, input_qna, similar_text, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    similar_text = similar_text.strip()
    text = '<q>' + input_text + '</s><t>' + input_qna + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len+1:])

        similarity_score = kiwi_evaluate_similarity(similar_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

In [93]:
model_name = 'kogpt2_qnacat_120000_4epoch_0.16569loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')


mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = Kiwi_QnA_valid_sim_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.5333081474429682, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(0.5757914543151855, '테라죠는 기대수명이 30년인 것으로 알려져 있습니다. 이는 우수한 품질의 테라죠 제품을 제대로 유지보수하고 적절히 관리했을 경우의 수명입니다. 올바른 관리와 유지보수가 이루어지면 테라죠 바닥은 오랫동안 사용할 수 있을 것입니다.')
(0.5333081474429682, '테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 이는 일반적인 사용 조건에서의 추정치이며, 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명이 달라질 수 있습니다. 따라서 테라죠의 수명을 늘리고자 하는 경우에는 제조사의 권장사례를 따르는 것이 좋습니다.')
(0.9999999433755875, '테라죠의 기대수명은 30년입니다.')
(0.9999999433755875, '테라죠의 기대수명은 30년입니다.')
테라죠의 기대수명은 30년입니다.

플로킹 벽지란 무엇을 의미하나요?
(0.9999997735023498, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다.')
(0.9999997735023498, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 가격이 비싸고 내구성이 떨어지며 관리가 힘들다는 단점이 있습니다.')
(0.9999997735023498, '벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 고급스러운 분위기를 연출하며 포인트 용으로 적합하다는 장점이 있지만 

## epoch 5 : 0.9146506249904632

In [63]:
model_name = 'kogpt2_qnacat_120000_5epoch_0.15203loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')


mean_score = []
answer_list = []
for _, row in tqdm(valid_sim.iterrows(), total=valid_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = QnA_valid_sim_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list, valid_sim['답변_1'])]
print(np.mean(scores))

  0%|          | 0/100 [00:00<?, ?it/s]

테라죠의 평균 수명은 몇 년인가요?
(0.4662690305047565, '테라죠는 일반적으로 30년 정도 사용 가능한 것으로 알려져 있습니다. 그러나 제품의 사용 방법, 유지 보수 상태, 주변 환경 등에 따라 실제 수명은 다를 수 있습니다. 따라서 테라죠의 수명을 늘리기 위해서는 제조사의 권장 사례를 따르는 것이 좋습니다.')
(0.5787452773915397, '테라죠의 예상 수명은 일반적으로 30년입니다. 그러나 올바른 유지보수와 적절한 사용 조건이 갖추어진다면 더 오래 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달라질 수 있습니다. 유지보수는 매우 중요하며, 적절하게 이루어지면 테라죠의 수명을 연장하는 데 도움이 됩니다.')
(0.5787452773915397, '테라죠의 예상 수명은 일반적으로 30년입니다. 그러나 올바른 유지보수와 적절한 사용 조건이 갖추어진다면 더 오래 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달라질 수 있습니다. 유지보수는 매우 중요하며, 적절하게 이루어지면 테라죠의 수명을 연장하는 데 도움이 됩니다.')
(0.579236720667945, '테라죠의 예상 수명은 일반적으로 30년입니다. 그러나 적절한 유지보수와 올바른 사용 조건이 갖추어진다면 더 오래 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달라질 수 있습니다. 유지보수는 매우 중요하며, 적절하게 이루어지면 테라죠의 수명을 연장하는 데 도움이 됩니다.')
(0.5762829737083331, '테라죠의 예상 수명은 일반적으로 30년입니다. 그러나 올바른 유지보수와 적절한 사용 조건이 갖춰진다면 더 오랜 시간 사용할 수 있습니다. 특히, 사용 환경과 노출 정도에 따라 이 기간은 달라질 수 있습니다. 유지보수는 매우 중요하며, 적절하게 이루어지면 테라죠의 수명을 연장하는 데 도움이 됩니다.')
테라죠의 예상 수명은 일반적으로 30년입니다. 그러나 적절한 유지보수와 올바른 사용 조건이 갖추어진다면 

# 최종 결과 추론

In [66]:
test_qna_cat = pd.read_csv(f'{DATA_PATH}test_qna_cat.csv')
test_sim = pd.read_csv(f'{DATA_PATH}test_sim2.csv') # 답변 1과 비교
test_sim2 = pd.read_csv(f'{DATA_PATH}test_sim3.csv') # 답변 2와 비교

In [61]:
def Qna_Chatbot(input_text, input_qna, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    text = '<q>' + input_text + '</s><t>' + input_qna + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len:])

        similarity_score = evaluate_similarity(input_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

In [ ]:
def Chatbot(input_text, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    text = '<q>' + input_text + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len:])

        similarity_score = evaluate_similarity(input_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

In [73]:
# def get_qna_category(text):
#     qna_cat = []
#     if '장점|좋은점|좋은 점|이점|장단점' in text and '차이점' not in text: qna_cat.append('장점')
#     return qna_cat

In [74]:
# def get_similar_answer(text) :
#     text = text.strip().replace('"', '')
#     connect_lst = ['그리고', '또한', '또', '한편', '이며', '인지', '이고']

#     sim_question = []
#     sim_answer = [sim_answer]

#     for word in connect_lst :
#         text = text.split(word)

#     for i in text :
#         # train 질문 pool에서 가장 유사도 높은 것 뽑아야 함


#     return sim_answer


IndentationError: expected an indented block after 'for' statement on line 11 (<ipython-input-74-ea3e000b97cd>, line 14)

# TEST 모델 추론

In [71]:
test_qna = test_qna_cat['qna_category'].tolist()
test_qna[:10]

["['단점', '종류']",
 "['방법.대책', '원인.이유']",
 "['장점', '단점']",
 "['사용.효과', '방법.대책']",
 '[]',
 "['장점', '단점']",
 "['단점', '추천']",
 "['원인.이유']",
 "['원인.이유']",
 "['원인.이유']"]

In [72]:
 test_sim['qna_category'] = test_qna
 test_sim2['qna_category'] = test_qna

In [78]:
def Qna_Similarity_Chatbot(input_text, input_qna, similar_text, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    text = '<q>' + input_text + '</s><t>' + input_qna + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len+1:])

        similarity_score = evaluate_similarity(similar_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

## Qna Similarity : 답변 1과의 유사도

In [79]:
model_name = 'kogpt2_qnacat_120000_4epoch_0.16569loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')


mean_score_sim1 = []
answer_list_sim1 = []
for _, row in tqdm(test_sim.iterrows(), total=test_sim.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = Qna_Similarity_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list_sim1.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list_sim1, test_sim['유사_답변'])]
print(np.mean(scores))

  0%|          | 0/130 [00:00<?, ?it/s]

방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용하는 것에 어떤 단점이 있을까요?
(0.9936239792750432, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.9936239792750432, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.9936239792750432, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.9936239792750432, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.9936239792750432, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다

## Qna Similarity : 답변 2와의 유사도

In [80]:
model_name = 'kogpt2_qnacat_120000_4epoch_0.16569loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')


mean_score_sim2 = []
answer_list_sim2 = []
for _, row in tqdm(test_sim2.iterrows(), total=test_sim2.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    similar_text = row['유사_답변']
    input_qna = row['qna_category']
    answer, score = Qna_Similarity_Chatbot(text, input_qna, similar_text, model=model, tokenizer=tokenizer, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list_sim2.append(answer)
    mean_score.append(score)

scores = [cosine_score(target, pred) for pred, target in zip(answer_list_sim2, test_sim2['유사_답변'])]
print(np.mean(scores))

  0%|          | 0/130 [00:00<?, ?it/s]

방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용하는 것에 어떤 단점이 있을까요?
(0.5811253737913419, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.5811253737913419, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.5811253737913419, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.5811253737913419, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.5811253737913419, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다

In [89]:
test['qna_category'] = test_qna
test

id                                                 질문  \
0    TEST_000  방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용...   
1    TEST_001            도배지에 녹은 자국이 발생하는 주된 원인과 그 해결 방법은 무엇인가요?   
2    TEST_002    큐블럭의 단점을 알려주세요. 또한, 압출법 단열판을 사용하는 것의 장점은 무엇인가요?   
3    TEST_003  철골구조를 사용하는 고층 건물에서, 단열 효과를 높이기 위한 시공 방법은 무엇이 있...   
4    TEST_004                   도배지의 완전한 건조를 위해 몇 주 동안 기다려야 하나요?   
..        ...                                                ...   
125  TEST_125  분말 소화기를 사용할 때 주의해야 할 사항은 무엇인가요? 그리고 아파트 도배 평수를...   
126  TEST_126                          압출법 보온판의 가장 큰 장점은 무엇인가요?"   
127  TEST_127  평지붕의 누수 문제를 방지하기 위해 수성 벽체용 탄성 방수 도료를 사용하는 것이 어...   
128  TEST_128  석고수정이 발생하는 가장 큰 원인은 무엇인가요? 그리고 이를 해결하는 방법에 대해 ...   
129  TEST_129     카페트의 기대 수명은 얼마나 될까요? 그리고 오리지널징크의 장점에는 무엇이 있나요?   

               qna_category  
0              ['단점', '종류']  
1        ['방법.대책', '원인.이유']  
2              ['장점', '단점']  
3        ['사용.효과', '방법.대책']  
4                        []  
..                      ...  
125  ['주의점', '설명', '측정.기준']  
126                  ['장점']  
127         ['장점', '방법.대책']  
128      ['방법.대책', '원인.이유']  
129         ['장점', '수명.주기']  

[130 rows x 3 columns]

## Qna  : 질문과의 유사도

In [85]:
def Qna_Chatbot(input_text, input_qna, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    text = '<q>' + input_text + '</s><t>' + input_qna + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len+1:])

        similarity_score = evaluate_similarity(input_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

In [90]:
mean_score = []
answer_list = []
for _, row in tqdm(test.iterrows(), total=test.shape[0]):
    reset_seeds(SEED)
    text = row['질문']
    input_qna = row['qna_category']
    answer, score = Qna_Chatbot(text, input_qna, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95)
    answer_list.append(answer)
    mean_score.append(score)

  0%|          | 0/130 [00:00<?, ?it/s]

방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용하는 것에 어떤 단점이 있을까요?
(0.1919466406871111, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.1919466406871111, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.1919466406871111, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.1919466406871111, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
(0.1919466406871111, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.')
방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다

## 비교 ***

In [91]:
for a, b, c,d in zip(test['질문'].tolist(), answer_list,answer_list_sim1, answer_list_sim2 ) :
    print(f'질문 : {a}')
    print(f'답변 질문 : {b}')
    print(f'답변 sim1: {c}')
    print(f'답변 sim2: {d}')
    print(' ')

질문 : 방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용하는 것에 어떤 단점이 있을까요?
답변 질문 : 방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.
답변 sim1: 방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.
답변 sim2: 방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.
 
질문 : 도배지에 녹은 자국이 발생하는 주된 원인과 그 해결 방법은 무엇인가요?
답변 질문 : 도배지에 녹이 묻어나오는 것은 녹오염으로, 도배지 상에 녹색 또는 갈색의 녹이 발생하는 현상을 의미합니다. 이러한 현상이 발생하는 원인, 책임소재 및 해결 방법은 다음과 같습니다. 1. 습도 문제 원인: 높은 습도로 인해 도배지 안쪽의 금속이 녹을 수 있습니다. 책임소재: 건물의 소유자나 거주자가 습기 관리의 책임이 있습니다. 해결 방법: 제습기 가동, 환기를 통해 실내 적정 습도를 유지하고 전문가의 도움을 받아 보수작업하는 것이 권장됩니다. 2. 누수 원인: 누수로 도배지가 젖은 상태가 계속되면 곰팡이가 발생할 수 있습니다. 책임소재: 건물의 소유자나 거주자가 책임이 있습니다. 해결 방법: 누수를 해결하고 곰팡이가 발생한 부분을 교체하거나 전체를 보수작업을 통해 처리합니다. 해당 작업은 전문가의 도움을 받는 것을 

In [122]:
answer_list_sim1

['방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.',
 '해당 현상은 녹 오염으로 도배지에 붉은색의 녹이 생기는 현상입니다. 도배지에 녹오염이 발생하는 원인 - 책임소재 - 해결방법에 대해 설명드리겠습니다. 1. 공간 내 높은 습도 원인 : 높은 습기로 인해 도배지 안쪽의 금속의 녹이 도배지에 베어나올 수 있습니다. 책임소재 : 건물의 소유자나 거주자가 습기 관리의 책임이 있습니다. 해결 방법 : 제습기 가동, 환기를 통해 실내 적정 습도를 유지하고 전문가의 도움을 받아 보수작업하는 것을 추천합니다. 2. 누수 원인 : 누수에 의해 도배지가 젖어 있는 상태가 지속되면 곰팡이가 발생할 수 있습니다. 책임소재 : 건물의 소유자나 거주자가 책임이 있습니다. 해결 방법 : 보수작업을 통해 누수를 제거하고 곰팡이가 발생한 도배지의 부분 및 전체를 교체해야 합니다.',
 '큐블럭은 일반 벽돌에 비해 가격이 비싸고 균열이 생기기 쉬우며 습기로 인해 하자가 발생할 수 있다는 점이 단점입니다. 또한, 압출법 단열판은 습기에 강하고 곰팡이 및 세균 증식을 막을 수 있으며 단열재 중 열전도율이 가장 낮은 편이고 시공이 간편하다는 장점이 있습니다.',
 '고층 건물을 짓는 데 있어서 가장 효과적인 방법은 단열재를 사용하는 것입니다. 단열재는 비용적으로 저렴하고 쉽게 사용할 수 있는 장점이 있지만, 열 전달 특성 때문에 단열재가 없는 벽에는 부적합하게 시공할 수 있으며, 찢어지면 큰 문제가 발생할 수 있습니다. 따라서 이러한 문제를 해결하기 위해서는 제습기나 환기를 통해 실내 습도를 조절하고, 단열재 성능을 개선하는 것이 필요합니다.',
 '도배지의 끝 부분이 들뜨는 경우, 이는 도배지가 벽면에 부착되지 않은 상태에서 발생하는 문제입니다. 따라서 도배지의 들뜸 현상을 

In [127]:
answer_list_sim2

['방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩의 단점은 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점입니다.',
 '도배지에 녹이 묻어나오는 것은 녹오염으로, 도배지 상에 녹색 또는 갈색의 녹이 발생하는 현상을 의미합니다. 이러한 현상이 발생하는 원인, 책임소재 및 해결 방법은 다음과 같습니다. 1. 습도 문제 원인: 높은 습도로 인해 도배지 안쪽의 금속이 녹을 수 있습니다. 책임소재: 건물의 소유자나 거주자가 습기 관리의 책임이 있습니다. 해결 방법: 제습기 가동, 환기를 통해 실내 적정 습도를 유지하고 전문가의 도움을 받아 보수작업하는 것이 권장됩니다. 2. 누수 원인: 누수로 도배지가 젖은 상태가 계속되면 곰팡이가 발생할 수 있습니다. 책임소재: 건물의 소유자나 거주자가 책임이 있습니다. 해결 방법: 누수를 해결하고 곰팡이가 발생한 부분을 교체하거나 전체를 보수작업을 통해 처리합니다. 해당 작업은 전문가의 도움을 받는 것을 추천드립니다.',
 '큐블럭은 일반 벽돌에 비해 가격이 비싸고 균열이 생기기 쉬우며 습기로 인해 하자가 발생할 수 있다는 점이 단점입니다. 또한, 압출법단 단열판은 습기에 강하고 곰팡이 및 세균 증식을 막을 수 있으며 단열재 중 열전도율이 가장 낮은 편이고 시공이 간편하다는 장점이 있습니다.',
 '고층 건물을 짓는 데 있어서 가장 효과적인 방법은 단열재를 사용하는 것입니다. 단열재는 비용적으로 저렴하고 쉽게 사용할 수 있는 장점이 있지만, 열 전달 특성 때문에 단열재가 없는 벽에는 부적합하게 시공할 수 있으며, 찢어지면 큰 문제가 발생할 수 있습니다. 따라서 이러한 문제를 해결하기 위해서는 제습기나 환기를 통해 실내 습도를 조절하고, 단열재 성능을 개선하는 것이 필요합니다.',
 '도배지의 끝 부분이 들뜨는 경우, 이는 도배지가 벽면에 부착되지 않은 상태에서 발생하는 문제입니다

In [128]:
vector_model = SentenceTransformer('distiluse-base-multilingual-cased-v1')
pred_vector = vector_model.encode(answer_list_sim1)
pred_vector.shape

(130, 512)

In [129]:
submission = pd.read_csv(f'{DATA_PATH}sample_submission.csv')
submission.iloc[:,1:] = pred_vector
submission

id     vec_0     vec_1     vec_2     vec_3     vec_4     vec_5  \
0    TEST_000  0.026558 -0.020150  0.015123  0.017831  0.064715  0.018982   
1    TEST_001 -0.011238 -0.029049  0.023131  0.006856  0.054049  0.001322   
2    TEST_002  0.026666 -0.047918 -0.023076 -0.000899  0.122727 -0.054804   
3    TEST_003 -0.019820 -0.028093 -0.015408  0.036968  0.090501 -0.037548   
4    TEST_004 -0.005152 -0.002174 -0.038554  0.015129  0.106112 -0.007910   
..        ...       ...       ...       ...       ...       ...       ...   
125  TEST_125  0.031945 -0.040357  0.029159  0.017422  0.122405 -0.065264   
126  TEST_126  0.044670 -0.001803 -0.023473  0.049179  0.073905 -0.050932   
127  TEST_127 -0.021847  0.011385 -0.006315  0.025524  0.093174 -0.018331   
128  TEST_128  0.036386 -0.027929 -0.063045  0.015607  0.084918 -0.076239   
129  TEST_129  0.010164 -0.022649  0.009348 -0.019028  0.067019 -0.040448   

        vec_6     vec_7     vec_8  ...   vec_502   vec_503   vec_504  \
0    0.002021 -0.006165 -0.006314  ... -0.013723 -0.000593 -0.031992   
1   -0.020075 -0.003844 -0.000223  ...  0.008023 -0.001149  0.007743   
2   -0.028414 -0.024834  0.044091  ... -0.034904 -0.016536  0.026996   
3    0.009847  0.000174  0.021601  ... -0.045278 -0.046328  0.069531   
4    0.046806  0.002844 -0.048501  ... -0.028052 -0.047972  0.031360   
..        ...       ...       ...  ...       ...       ...       ...   
125  0.065536  0.044294  0.046401  ...  0.009230  0.011533  0.046260   
126 -0.020283  0.015079  0.033669  ... -0.038939 -0.056673 -0.013285   
127 -0.015956 -0.039007 -0.020609  ... -0.026562 -0.024477 -0.008095   
128  0.011936  0.024018 -0.014002  ... -0.026435 -0.025367  0.003164   
129 -0.037926  0.027617  0.110329  ... -0.038511  0.046827 -0.035261   

      vec_505   vec_506   vec_507   vec_508   vec_509   vec_510   vec_511  
0   -0.039757  0.001512  0.022232  0.030489  0.040009  0.001398  0.013257  
1   -0.045182 -0.038391  0.036908  0.006009 -0.036735  0.039681 -0.006677  
2   -0.023931  0.023183  0.012665 -0.041810 -0.040179 -0.048819  0.092766  
3   -0.041483 -0.006487  0.043106 -0.016461 -0.052907  0.003943  0.101319  
4   -0.021900 -0.033814  0.061567  0.010740 -0.021115  0.001195  0.072144  
..        ...       ...       ...       ...       ...       ...       ...  
125 -0.034025  0.015086  0.053933  0.044437 -0.020994 -0.027847  0.007961  
126 -0.030416  0.060896  0.042285 -0.002789 -0.050393  0.003319  0.079439  
127 -0.016211 -0.032782  0.045392  0.022317  0.027755 -0.035980  0.030674  
128 -0.060882 -0.018098  0.008412  0.012525 -0.015694  0.026506  0.010083  
129 -0.005463 -0.006967  0.057649 -0.091274  0.057718 -0.056928 -0.014354  

[130 rows x 513 columns]

In [130]:
submission.to_csv(f'{SUBMISSION_PATH}sim2_hansol_qna_cat_120000_4ep_0311.csv', index=False)
submission.to_csv(f'sim2_hansol_qna_cat_120000_4ep_0311.csv', index=False)

## Kiwi Qna : 질문과의 키위 유사도

In [ ]:
def Kiwi_Qna_Chatbot(input_text, input_qna, model=model, tokenizer=tokenizer, device=device,
            max_length=200, temperature=0.87, top_k=27, top_p=0.7, num_samples=5, generated=True):

    model.eval()
    input_text = input_text.strip().replace('"', '')
    print(input_text)
    text = '<q>' + input_text + '</s><t>' + input_qna + '</s><a>'
    input_ids = tokenizer.encode(text, return_tensors='pt').to(device)
    q_len = len(text) + 1

    best_generated_text = None
    best_similarity_score = -1.0
    score_lst = []
    generated_texts = []
    for i in range(num_samples):
        result_ids = model.generate(input_ids,
                                    max_length=max_length,
                                    temperature=temperature,
                                    top_k=top_k,
                                    top_p=top_p,
                                    do_sample=True,
                                    num_return_sequences=1,
                                    )

        generated_text = tokenizer.decode(result_ids[0])
        generated_text = post_processing(generated_text[q_len+1:])

        similarity_score = evaluate_similarity(input_text, generated_text)
        score_lst.append(similarity_score)
        generated_texts.append((similarity_score,generated_text))
        if generated:
            print(generated_texts[i]) # 실제 돌릴땐 off

        if similarity_score > best_similarity_score:
            best_similarity_score = similarity_score
            best_generated_text = generated_text

    if '?' in best_generated_text :
        continue

    print(best_generated_text)
    print()

    return best_generated_text, score_lst

In [ ]:
from sentence_transformers import SentenceTransformer
from sklearn.metrics.pairwise import pairwise_distances
embedding_model = SentenceTransformer('distiluse-base-multilingual-cased-v1')

def get_kiwi_nouns(text):
    pos_result = kiwi.tokenize(text)
    nouns = [word for word, pos, _,_ in pos_result if pos.startswith('N')]
    return ' '.join(nouns)

def kiwi_evaluate_similarity(input_text, generated_text, alpha=0.95): # cosine 가중치 조절

    input_embedding = embedding_model.encode(get_kiwi_nouns(input_text))
    generated_embedding = embedding_model.encode(get_kiwi_nouns(generated_text))

    # 코사인 유사도
    cosine_sim = 1 - pairwise_distances([input_embedding], [generated_embedding], metric='cosine')[0][0]

    # 자카드 유사도
    input_tokens = set(input_text.split())
    generated_tokens = set(generated_text.split())
    jaccard_sim = len(input_tokens.intersection(generated_tokens)) / len(input_tokens.union(generated_tokens))

    # 가중 평균 내보기
    weighted_sim = alpha*cosine_sim + (1 - alpha)*jaccard_sim

    return weighted_sim

In [71]:
model_name = 'kogpt2_qnacat_120000_3epoch_0.19047loss'

model = GPT2LMHeadModel.from_pretrained(f'{DATA_PATH}model/{model_name}').to(device)
tokenizer = AutoTokenizer.from_pretrained("skt/kogpt2-base-v2",
                                                    bos_token='</s>',
                                                    eos_token='</s>',
                                                    unk_token='<unk>',
                                                    pad_token='<pad>',
                                                    mask_token='<mask>')

mean_score = []
answer_list = []
for text in tqdm(test['질문'].tolist()) :
    reset_seeds(SEED)
    answer, score = Chatbot(text, generated=True, max_length=200, temperature=0.5, top_k=20, top_p=0.95) # 기 제출
    answer_list.append(answer)
    mean_score.append(score)

  0%|          | 0/130 [00:00<?, ?it/s]

방청 페인트의 종류에는 어떤 것들이 있는지 알고 계신가요? 또한, 원목사이딩을 사용하는 것에 어떤 단점이 있을까요?
(0.2246882709173056, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩을 사용하는 경우 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점이 단점입니다.')
(0.2246882709173056, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩을 사용하는 경우 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점이 단점입니다.')
(0.2246882709173056, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩을 사용하는 경우 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점이 단점입니다.')
(0.2246882709173056, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩을 사용하는 경우 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점이 단점입니다.')
(0.2246882709173056, '방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트, 역청질페인트, 워시프라이머, 크롬산아연페인트, 규산염페인트가 있습니다. 또한, 원목사이딩을 사용하는 경우 가격대가 높고 관리가 어려우며 습기에 약해 뒤틀림, 부서짐, 수축/팽장이 생길 수 있다는 점이 단점입니다.')
방청페인트의 종류는 광명단페인트, 방청산화철페인트, 알미늄페인트

In [ ]:
for a, b, c in zip(test['질문'].tolist(), answer_list, mean_score) :
    print(f'질문 : {a}')
    print(f'답변 : {b}')
    print(f'답변 : {c}')
    print(' ')

질문 : 테라죠의 평균 수명은 몇 년인가요?
답변 : 테라죠는 흔히 30년 정도의 기대수명을 가지고 있습니다. 그러나 올바른 유지보수와 적절한 사용 환경에서는 이 기간을 늘릴 수 있습니다. 올바른 관리와 보수가 이루어지면 테라죠의 수명을 늘릴 수 있으니 주의해야 합니다.
답변 : [0.43413846492767333, 0.5552318149142795, 0.47361934304237363, 0.5798271965097498, 0.5197723836974895]
 
질문 : 플로킹 벽지란 무엇을 의미하나요?
답변 : 플로킹 벽지는 벨벳 소재를 사용하여 입체감을 살린 벽지입니다. 이러한 벽지는 고급스러운 분위기를 연출하며 포인트로 활용하기에 적합합니다. 하지만, 가격이 비싸고 내구성이 떨어지며 관리가 어렵다는 단점이 있습니다. 특히, 플로킹 벽지는 습기에 쉽게 영향을 받으며 관리하기 어렵다는 단점이 있습니다.
답변 : [0.5874197787963427, 0.7324276877774133, 0.6170787886102149, 0.7252368763514927, 0.6634041263506962]
 
질문 : 건조는 며칠 동안 진행되어야 하나요?
답변 : 건조는 건조시간이 필요하기 때문에 일주일이 걸릴 수 있습니다. 건조기간 동안에는 온도와 습도에 유의해야 하며, 일주일이 지난 후에도 도배지가 완전히 건조되지 않았다면 전문가의 조언이 필요합니다.
답변 : [0.24134649634361266, 0.49570566591094517, 0.645196030821119, 0.510440013068063, 0.32875890433788296]
 
질문 : 장판의 장점이 뭔가요?
답변 : 장판은 단가와 시공비가 저렴하고 보행감이 좋으며 높은 열전도율로 난방효과가 좋고 층간 소음 방지에 좋다는 장점이 있습니다.
답변 : [0.6707594820044257, 1.0, 0.9889704791938557, 1.0, 0.37138307612193255]
 
질문 : 도막방수공사는 어떤